# Fine-tuning LLMs for Auto Issue Diagnosis with Databricks Mosaic AI

## Fine Tuning or RAG?
RAG and fine-tuning can work together! If you have a relevant RAG use-case, you can start with RAG leveraging a foundational model, and then specialize your model if your corpus is specific to your business (ex: not part of the foundation model training) or need specific behavior (ex: answer to a specific task such as entity extraction)


Start with RAG on a Foundation Model, evaluate how your model is working and where it can be improved, and build a Fine Tuned dataset accordingly!

However, in this case, **we're going to use our car forum data to build a fine tuned LLM**


In [0]:
# Let's start by installing our libraries
%pip install --quiet databricks-genai==1.1.4 mlflow==2.16.2
%pip install --quiet databricks-sdk==0.40.0
dbutils.library.restartPython()

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
databricks-genai 1.1.4 requires databricks-sdk==0.29.0, but you have databricks-sdk 0.40.0 which is incompatible.
Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
catalog = 'main'
schema = 'sgfs'
training_table = f"{catalog}.{schema}.reasoning_traces_quant_distill_r1_llama70b"
base_model_name = "meta-llama/Meta-Llama-3.1-70B-Instruct"

In [0]:
training_dataset = spark.sql(f"""
  SELECT instruction as question, input as content, answer from {training_table} where answer is not null
      """)
display(training_dataset)

question content answer Answer the following question after understanding the specifics of the vehicle in question.

It is a 2000 Toyota Sienna CE 3.0L Dash lights. with the VIN 4T3GF19C2YU310996 and a mileage of 65,500 mi. This 2000 Toyota Sienna CE is a 3.0L / 6 cyl / Gas engine with 4-speed Automatic Transaxle (Electronic) transmission.
Delivery system: Fuel Injection Affected component: Dash Lights Conditions: Shorted This vehicle has 2 separate fuses for the lights. The one that is blowing is for the dash lights. The parking light fuse is O.K. As soon as you turn on the parking light switch, it has a dead short to to the dash light fuse. I checked the switch and can't find anything wrong with it. My short finder won't stay on long enough to find the affected area. I went ahead and connected a wire across the fuse real quick to find the problem. It had some smoke come out of the harness under the dash, but couldn't tell because it was in the middle of a harness full of about 50 wires. At this point it could still be something behind the instrument panel, a component, etc. Has anyone seen this on this vehicle before? I need some info before I go any further. Alright, let's tackle this dash light issue on your 2000 Toyota Sienna step by step.

1. **Check for Aftermarket Installations**: Start by inspecting any aftermarket components like stereos or accessories near the dash. Improper wiring, especially grounding issues, can cause shorts when switches are activated.

2. **Inspect Visor Wires**: Remove the visors and check for pinched wires in the headliner, a common issue that can lead to shorts.

3. **Verify Bulbs**: Ensure all bulbs are correctly installed as incorrect types might cause unexpected electrical behavior.

4. **Review Accident History**: Consider if past accidents or repairs could have affected wiring integrity, even if unrelated at first glance.

5. **Disconnect Accessories**: If equipped with a trailer harness or similar, temporarily disconnect it to rule out external issues.

6. **Use Proper Diagnostic Tools**: Invest in a good multimeter with an amp clamp to safely and accurately trace the short without causing further damage.

By systematically checking these areas, you should be able to identify and resolve the cause of your dash light fuse blowing. Answer the following question after understanding the specifics of the vehicle in question.

It is a 1998 Isuzu Trooper S 3.5L Timing Belt. with the VIN JACDJ58X1W7905214 and a mileage of 81,000 mi. This 1998 Isuzu Trooper S is a 3.5L / 6 cyl / Gas engine with 4-speed Automatic Transmission transmission.
Delivery system: Fuel Injection Affected component: Timing Belt I am trying to set up the timing belt on this 3.5 trooper, the camshafts were turned while the timing belt was removed. I read the tsb (IB00-S005) and set the cams back the way it describes. I line up all of the lines on the timing belt and I have to turn the crankshaft 3 turns to get the timing marks to line back up on the engine. Am I doing something wrong or is this normal? Step29 of the tsb says to turn the crank a "minimum of 2 complete turns" is this saying what I think it does and I may have to turn the crank 3 times? Please help. thank you. The situation you're encountering with your 1998 Isuzu Trooper S 3.5L engine is quite normal, especially given the engine's unique timing setup. Here's a concise summary of what you need to know and do:

1. **Normal Multiple Turns**: It's normal for the timing marks to align only after more than two crankshaft rotations because each cam sprocket drives two gears, requiring additional turns to sync everything.

2. **Focus on Engine Marks**: Rely on the engine's own timing marks on the crank and cam sprockets rather than the belt's marks, as these are more critical for accurate alignment.

3. **TSB Guidance**: The TSB mentions a minimum of two turns, but it may require three or more rotations to achieve proper alignment due to the engine's design quirks.


## Preparing the Dataset for Chat Completion

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/llm-fine-tuning/databricks-llm-fine-tuning-2.png?raw=true" width="700px" style="float: right">

Because we're fine tuning a chatbot, we need to prepare our dataset for **Chat completion**.

Chat completion requires a list of **role** and **prompt**, following the OpenAI standard. This standard has the benefit of transforming our input into a prompt following our LLM instruction pattern. <br/>
Note that each foundation model might be trained with a different instruction type, so it's best to use the same type when fine tuning.<br/>
*We recommend using Chat Completion whenever possible.*

```
[
  {"role": "system", "content": "[system prompt]"},
  {"role": "user", "content": "Here is a documentation page:[RAG context]. Based on this, answer the following question: [user question]"},
  {"role": "assistant", "content": "[answer]"}
]
```


#### Training Data Type

Databricks supports a large variety of dataset formats (Volume files, Delta tables, and public Hugging Face datasets in .jsonl format), but we recommend preparing the dataset as Delta tables within your Catalog as part of a proper data pipeline to ensure production quality.
*Remember, this step is critical and you need to make sure your training dataset is of high quality.*

Let's create a small pandas UDF to help create our final chat completion dataset.<br/>

In [0]:
from pyspark.sql.functions import pandas_udf
import pandas as pd

system_prompt = """You are an agent that helps with resolving user issues with their car. Your job is to post a helpful response while showing that you deeply care about solving the problem to the best of your ability. Be factual,structured and focus on the utility and relevance of your response.\n"""

@pandas_udf("array<struct<role:string, content:string>>")
def create_conversation(content: pd.Series, question: pd.Series, answer: pd.Series) -> pd.Series:
    def build_message(c,q,a):
        user_input = f"{q} :\n {c}"
        if "mistral" in base_model_name:
            #Mistral doesn't support system prompt
            return [
                {"role": "user", "content": f"{system_prompt} \n{user_input}"},
                {"role": "assistant", "content": a}]
        else:
            return [
                {"role": "system", "content": system_prompt},
                {"role": "user", "content": user_input},
                {"role": "assistant", "content": a}]
    return pd.Series([build_message(c,q,a) for c, q, a in zip(content, question, answer)])


# training_data, eval_data = training_dataset.randomSplit([0.9, 0.1], seed=42)

training_dataset.select(create_conversation("content", "question", "answer").alias('messages')).write.mode('overwrite').saveAsTable(f"{catalog}.{schema}.forum_completion_training_dataset")
# eval_data.write.mode('overwrite').saveAsTable("chat_completion_evaluation_dataset")

display(spark.table(f'{catalog}.{schema}.forum_completion_training_dataset'))

messages List(List(system, You are an agent that helps with resolving user issues with their car. Your job is to post a helpful response while showing that you deeply care about solving the problem to the best of your ability. Be factual,structured and focus on the utility and relevance of your response.
), List(user, Answer the following question after understanding the specifics of the vehicle in question.

It is a 2000 Toyota Sienna CE 3.0L Dash lights. with the VIN 4T3GF19C2YU310996 and a mileage of 65,500 mi. This 2000 Toyota Sienna CE is a 3.0L / 6 cyl / Gas engine with 4-speed Automatic Transaxle (Electronic) transmission.
Delivery system: Fuel Injection Affected component: Dash Lights Conditions: Shorted :
 This vehicle has 2 separate fuses for the lights. The one that is blowing is for the dash lights. The parking light fuse is O.K. As soon as you turn on the parking light switch, it has a dead short to to the dash light fuse. I checked the switch and can't find anything wrong with it. My short finder won't stay on long enough to find the affected area. I went ahead and connected a wire across the fuse real quick to find the problem. It had some smoke come out of the harness under the dash, but couldn't tell because it was in the middle of a harness full of about 50 wires. At this point it could still be something behind the instrument panel, a component, etc. Has anyone seen this on this vehicle before? I need some info before I go any further.), List(assistant, Alright, let's tackle this dash light issue on your 2000 Toyota Sienna step by step.

1. **Check for Aftermarket Installations**: Start by inspecting any aftermarket components like stereos or accessories near the dash. Improper wiring, especially grounding issues, can cause shorts when switches are activated.

2. **Inspect Visor Wires**: Remove the visors and check for pinched wires in the headliner, a common issue that can lead to shorts.

3. **Verify Bulbs**: Ensure all bulbs are correctly installed as incorrect types might cause unexpected electrical behavior.

4. **Review Accident History**: Consider if past accidents or repairs could have affected wiring integrity, even if unrelated at first glance.

5. **Disconnect Accessories**: If equipped with a trailer harness or similar, temporarily disconnect it to rule out external issues.

6. **Use Proper Diagnostic Tools**: Invest in a good multimeter with an amp clamp to safely and accurately trace the short without causing further damage.

By systematically checking these areas, you should be able to identify and resolve the cause of your dash light fuse blowing.)) List(List(system, You are an agent that helps with resolving user issues with their car. Your job is to post a helpful response while showing that you deeply care about solving the problem to the best of your ability. Be factual,structured and focus on the utility and relevance of your response.
), List(user, Answer the following question after understanding the specifics of the vehicle in question.

It is a 1998 Isuzu Trooper S 3.5L Timing Belt. with the VIN JACDJ58X1W7905214 and a mileage of 81,000 mi. This 1998 Isuzu Trooper S is a 3.5L / 6 cyl / Gas engine with 4-speed Automatic Transmission transmission.
Delivery system: Fuel Injection Affected component: Timing Belt :
 I am trying to set up the timing belt on this 3.5 trooper, the camshafts were turned while the timing belt was removed. I read the tsb (IB00-S005) and set the cams back the way it describes. I line up all of the lines on the timing belt and I have to turn the crankshaft 3 turns to get the timing marks to line back up on the engine. Am I doing something wrong or is this normal? Step29 of the tsb says to turn the crank a "minimum of 2 complete turns" is this saying what I think it does and I may have to turn the crank 3 times? Please help. thank you.), List(assistant, The situation you're encountering with your 1998 Isuzu Trooper S 3.5L engine is quite normal, especially given t


## Starting a Fine Tuning Run


Once the training is done, your model will automatically be saved within Unity Catalog and available for you to serve!

In [0]:
from databricks.model_training import foundation_model as fm
import re
#Return the current cluster id to use to read the dataset and send it to the fine tuning cluster. See https://docs.databricks.com/en/large-language-models/foundation-model-training/create-fine-tune-run.html#cluster-id
def get_current_cluster_id():
  import json
  return json.loads(dbutils.notebook.entry_point.getDbutils().notebook().getContext().safeToJson())['attributes']['clusterId']


#Let's clean the model name
registered_model_name = f"{catalog}.{schema}." + re.sub(r'[^a-zA-Z0-9]', '_',  base_model_name)



run = fm.create(
    experiment_path='/Users/sathish.gangichetty@databricks.com/ift-meta-llama-3-1-70b-instruct-ffdljl',
    # custom_weights_path='dbfs:/databricks/mlflow-tracking/2507833646457908/a5156cb0d48f44309d16e6e7b427d540/artifacts/ift-meta-llama-3-1-70b-instruct-ffdljl/checkpoints/ep5-ba30',
    data_prep_cluster_id=get_current_cluster_id(),  # required if you are using delta tables as training data source. This is the cluster id that we want to use for our data prep job.
    model=base_model_name,  # Here we define what model we used as our baseline
    train_data_path=f"{catalog}.{schema}.forum_completion_training_dataset",
    task_type="CHAT_COMPLETION",  # Change task_type="INSTRUCTION_FINETUNE" if you are using the fine-tuning API for completion.
    register_to=registered_model_name,
    training_duration="10ep", #only 5 epoch to start. Check the mlflow experiment metrics to see if you should increase this number
    learning_rate="5e-7",
)

print(run)

TrainingRun(name='ift-meta-llama-3-1-70b-instruct-yc73zl', status=<RunStatus.PENDING: 'PENDING'>, created_by='sathish.gangichetty@databricks.com', model='meta-llama/Meta-Llama-3.1-70B-Instruct', save_folder='dbfs:/databricks/mlflow-tracking/{mlflow_experiment_id}/{mlflow_run_id}/artifacts', train_data_path='main.sgfs.forum_completion_training_dataset', register_to='main.sgfs.meta_llama_Meta_Llama_3_1_70B_Instruct', submitted_experiment_path='/Users/sathish.gangichetty@databricks.com/ift-meta-llama-3-1-70b-instruct-ffdljl', task_type='CHAT_COMPLETION', eval_data_path=None, eval_prompts=[], custom_weights_path=None, training_duration='10ep', learning_rate=5e-07, context_length=8192, data_prep_cluster_id='0118-165440-l8erfx3g', details='The service is currently experiencing high demand. Your run will start as soon as compute becomes available.', created_at=datetime.datetime(2025, 3, 2, 18, 8, 2, 34000, tzinfo=datetime.timezone.utc), started_at=None, estimated_end_time=None, formatted_eta=

#### 1.2) Tracking Fine Tuning Runs via the MLFlow Experiment

To monitor the progress of an ongoing or past fine tuning run, you can open the run from the MLFlow Experiment. Here you will find valuable information on how you may wish to tweak future runs to get better results. For example:
* Adding more epochs if you see your model still improving at the end of your run
* Increasing learning rate if loss is decreasing, but very slowly
* Decreasing learning rate if loss is fluctuating widely

<img src="https://github.com/databricks-demos/dbdemos-resources/blob/main/images/product/llm-fine-tuning/databricks-llm-fine-tuning-experiment.png?raw=true" width="1200px">

In [0]:
displayHTML(f'Open the <a href="/ml/experiments/{run.experiment_id}/runs/{run.run_id}/model-metrics">training run on MLFlow</a> to track the metrics')
#Track the run details
display(run.get_events())


def wait_for_run_to_finish(run):
  import time
  for i in range(300):
    events = run.get_events()
    for e in events:
      if "FAILED" in e.type or "EXCEPTION" in e.type:
        raise Exception(f'Error with the fine tuning run, check the details in run.get_events(): {e}')
    if events[-1].type == 'COMPLETED':
      print('Run finished')
      display(events)
      return events
    if i % 30 == 0:
      print(f'waiting for run {run.name} to complete...')
    time.sleep(10)


#helper function waiting on the run to finish - see the _resources folder for more details
wait_for_run_to_finish(run)

Open the training run on MLFlow to track the metrics

List[TrainingEvent(type='CREATED', time='2025-03-02T18:08:02.034Z', message='Run created.')]

waiting for run ift-meta-llama-3-1-70b-instruct-yc73zl to complete...
waiting for run ift-meta-llama-3-1-70b-instruct-yc73zl to complete...
waiting for run ift-meta-llama-3-1-70b-instruct-yc73zl to complete...
waiting for run ift-meta-llama-3-1-70b-instruct-yc73zl to complete...
waiting for run ift-meta-llama-3-1-70b-instruct-yc73zl to complete...
waiting for run ift-meta-llama-3-1-70b-instruct-yc73zl to complete...
Run finished


List[TrainingEvent(type='CREATED', time='2025-03-02T18:08:02.034Z', message='Run created.'), TrainingEvent(type='STARTED', time='2025-03-02T18:08:32.177Z', message='Run started.'), TrainingEvent(type='DATA_VALIDATED', time='2025-03-02T18:10:58.759Z', message='Training data validated.'), TrainingEvent(type='MODEL_INITIALIZED', time='2025-03-02T18:13:10.138Z', message='Model data downloaded and initialized for base model meta-llama/Meta-Llama-3.1-70B-Instruct.'), TrainingEvent(type='TRAIN_STARTED', time='2025-03-02T18:13:14.378Z', message='Training started.'), TrainingEvent(type='CHECKPOINT_SAVED', time='2025-03-02T18:31:44.680Z', message='Checkpoint saved.'), TrainingEvent(type='TRAIN_FINISHED', time='2025-03-02T18:37:50.948Z', message='Training completed.'), TrainingEvent(type='TRAIN_UPDATED', time='2025-03-02T18:37:51.255Z', message='[epoch=10/10][batch=0/3][ETA=0min] Train loss: 1.18'), TrainingEvent(type='COMPLETED', time='2025-03-02T18:38:11.420Z', message='Run completed.\n Final weights uploaded.')]

List[TrainingEvent(type='CREATED', time='2025-03-02T18:08:02.034Z', message='Run created.'), TrainingEvent(type='STARTED', time='2025-03-02T18:08:32.177Z', message='Run started.'), TrainingEvent(type='DATA_VALIDATED', time='2025-03-02T18:10:58.759Z', message='Training data validated.'), TrainingEvent(type='MODEL_INITIALIZED', time='2025-03-02T18:13:10.138Z', message='Model data downloaded and initialized for base model meta-llama/Meta-Llama-3.1-70B-Instruct.'), TrainingEvent(type='TRAIN_STARTED', time='2025-03-02T18:13:14.378Z', message='Training started.'), TrainingEvent(type='CHECKPOINT_SAVED', time='2025-03-02T18:31:44.680Z', message='Checkpoint saved.'), TrainingEvent(type='TRAIN_FINISHED', time='2025-03-02T18:37:50.948Z', message='Training completed.'), TrainingEvent(type='TRAIN_UPDATED', time='2025-03-02T18:37:51.255Z', message='[epoch=10/10][batch=0/3][ETA=0min] Train loss: 1.18'), TrainingEvent(type='COMPLETED', time='2025-03-02T18:38:11.420Z', message='Run completed.\n Final weights uploaded.')]

#### 1.3) Deploy Fine Tuned Model to a Serving Endpoint

<img src="https://docs.databricks.com/en/_images/create-provisioned-throughput-ui.png" width="600px" style="float: right">

Once ready, the model will be available in Unity Catalog.

From here, you can use the UI to deploy your model, or you can use the API. For reproducibility, we'll be using the API below:


In [0]:
def get_latest_model_version(model_name):
    from mlflow.tracking import MlflowClient
    mlflow_client = MlflowClient(registry_uri="databricks-uc")
    latest_version = 1
    for mv in mlflow_client.search_model_versions(f"name='{model_name}'"):
        version_int = int(mv.version)
        if version_int > latest_version:
            latest_version = version_int
    return latest_version

In [0]:
%sql
-- drop table if exists main.sgfs.aap_ft_70b_payload; this is a precondition if you need to deploy 

In [0]:
from databricks.sdk import WorkspaceClient
import re
from databricks.sdk.service.serving import (
    ServedEntityInput,
    EndpointCoreConfigInput,
    AiGatewayConfig,
    AiGatewayInferenceTableConfig
)

registered_model_name = f"{catalog}.{schema}." + re.sub(r'[^a-zA-Z0-9]', '_',  base_model_name)

serving_endpoint_name = "sg_llama31_70B_auto"
w = WorkspaceClient()

# Create the AI Gateway configuration
ai_gateway_config = AiGatewayConfig(
    inference_table_config=AiGatewayInferenceTableConfig(
        enabled=True,
        catalog_name=catalog,
        schema_name=schema,
        table_name_prefix="aap_ft_70b_distill"
    )
)

endpoint_config = EndpointCoreConfigInput(
    name=serving_endpoint_name,
    served_entities=[
        ServedEntityInput(
            entity_name=registered_model_name,
            entity_version=get_latest_model_version(registered_model_name),
            min_provisioned_throughput=0,
            max_provisioned_throughput=100,
            scale_to_zero_enabled=True
        )
    ]
)

force_update = False
existing_endpoint = next(
    (e for e in w.serving_endpoints.list() if e.name == serving_endpoint_name), None
)

if existing_endpoint is None:
    print(f"Creating the endpoint {serving_endpoint_name}, this will take a few minutes to package and deploy the endpoint...")
    w.serving_endpoints.create_and_wait(name=serving_endpoint_name, config=endpoint_config, ai_gateway=ai_gateway_config)
else:
    print(f"Endpoint {serving_endpoint_name} already exists...")
    if force_update:
        w.serving_endpoints.update_config_and_wait(
            served_entities=endpoint_config.served_entities,
            name=serving_endpoint_name
        )


Creating the endpoint sg_llama31_70B_auto, this will take a few minutes to package and deploy the endpoint...


#### 1.4) Testing the Model Endpoint

That's it! We're now ready to serve our Fine Tuned model and start asking questions!


In [0]:
import mlflow
from mlflow import deployments
#remove the answer to get only the system + user role.
test_dataset = spark.table('main.sgfs.forum_completion_training_dataset').selectExpr("slice(messages, 1, size(messages)-1) as messages").limit(1)
#Get the first messages
messages = test_dataset.toPandas().iloc[0].to_dict()['messages'].tolist()
print(messages)

[{'role': 'system', 'content': 'You are an agent that helps with resolving user issues with their car. Your job is to post a helpful response while showing that you deeply care about solving the problem to the best of your ability. Be factual,structured and focus on the utility and relevance of your response.\n'}, {'role': 'user', 'content': "Answer the following question after understanding the specifics of the vehicle in question.\n\nIt is a 2000 Toyota Sienna CE 3.0L Dash lights. with the VIN 4T3GF19C2YU310996 and a mileage of 65,500 mi. This 2000 Toyota Sienna CE is a 3.0L / 6 cyl / Gas engine with 4-speed Automatic Transaxle (Electronic) transmission.\nDelivery system: Fuel Injection Affected component: Dash Lights Conditions: Shorted :\n This vehicle has 2 separate fuses for the lights. The one that is blowing is for the dash lights. The parking light fuse is O.K. As soon as you turn on the parking light switch, it has a dead short to to the dash light fuse. I checked the switch 

In [0]:
client = mlflow.deployments.get_deploy_client("databricks")
client.predict(endpoint=serving_endpoint_name, inputs={"messages": messages, "max_tokens": 500})

{'id': 'chatcmpl_43f803f7-0239-4f50-a4fb-a36499f3a92b',
 'object': 'chat.completion',
 'created': 1740948490,
 'model': '',
 'choices': [{'index': 0,
   'message': {'role': 'assistant',
    'content': 'Around the Stereo Housing there is a red wire that is usually pinched as you route it back through the harness too far.\n\nThere are also mounts on the column that might be pinched.\n\nLooking under the dash is a wise observation to see if there is heat damage'},
   'finish_reason': 'stop',
   'logprobs': None}],
 'usage': {'prompt_tokens': 367, 'completion_tokens': 54, 'total_tokens': 421}}